In [1]:
#import numpy as np
#print(np.__version__)

In [1]:
from datasets import load_dataset

data_files = "E:/Hugging_Face/telecom_plans.csv"
plan_data = load_dataset("csv", data_files = data_files, split = "train")
plan_data[13]

E:\Anaconda\Lib\site-packages\pandas\core\arrays\masked.py:61: UserWarning: Pandas requires version '1.3.6' or newer of 'bottleneck' (version '1.3.5' currently installed).
  from pandas.core import (


{'Provider': 'Virgin Plus',
 'Plan Name': 'BYOP 40GB + 10GB Bonus (Add-a-line)',
 'Price': 40,
 'Data': '50GB',
 'BYOD': True,
 'Contract': 'No',
 'Hotspot': True,
 'Notes': 'Add-a-line'}

In [2]:
def description(example):
    if example['Notes'] == 'New':
        customer_note = 'new customers migrating from other service providers'
    elif example['Notes'] == 'Add-a-line':
        customer_note = f"adding a line on existing {example['Provider']} account"
    else:
        customer_note = 'hardware upgrade customers only'

    return {
        "Description": (
            f"{example['Provider']} offers a plan "
            f"{example['Plan Name']} for the price of ${example['Price']} a month, which includes {example['Data']} "
            f"data with {'BYOD' if example['BYOD'] else 'device financing over 24 months'} and "
            f"{'allows you to data-share with Hotspot' if example['Hotspot'] else 'does not include data-share with Hotspot'}. "
            f"This plan is for {customer_note}."
        )
    }

plan_data_mod = plan_data.map(description)
         

In [3]:
plan_data_mod[:5]

{'Provider': ['Bell', 'Bell', 'Bell', 'Bell', 'Bell'],
 'Plan Name': ['Elite Lite (New)',
  'Elite Lite (Add-a-line)',
  'Elite Lite (HUG)',
  'ExtraElite (New)',
  'ExtraElite (Add-a-line)'],
 'Price': [60, 60, 60, 45, 45],
 'Data': ['60GB', '60GB', '60GB', '50GB', '50GB'],
 'BYOD': [False, False, False, False, False],
 'Contract': ['SmartPay', 'SmartPay', 'SmartPay', 'SmartPay', 'SmartPay'],
 'Hotspot': [True, True, True, True, True],
 'Notes': ['New', 'Add-a-line', 'HUG', 'New', 'Add-a-line'],
 'Description': ['Bell offers a plan Elite Lite (New) for the price of $60 a month, which includes 60GB data with device financing over 24 months and allows you to data-share with Hotspot. This plan is for new customers migrating from other service providers.',
  'Bell offers a plan Elite Lite (Add-a-line) for the price of $60 a month, which includes 60GB data with device financing over 24 months and allows you to data-share with Hotspot. This plan is for adding a line on existing Bell account

In [4]:
#!pip uninstall urllib3 -y
#!pip install urllib3==1.26.18

In [5]:
#!pip install --upgrade accelerate transformers

In [6]:
from sentence_transformers import SentenceTransformer

embedder = SentenceTransformer("all-MiniLM-L6-v2")

descriptions = plan_data_mod["Description"]
embeddings = embedder.encode(descriptions, convert_to_numpy = True)

In [7]:
embeddings

array([[-0.04481903, -0.06913085,  0.02706613, ..., -0.08726593,
        -0.05549479,  0.00731448],
       [-0.05391502, -0.07286713, -0.00130842, ..., -0.07893781,
        -0.05440836, -0.02790258],
       [-0.0552901 , -0.04580358,  0.04743244, ..., -0.10154203,
        -0.05256264,  0.02625924],
       ...,
       [ 0.00983924,  0.01232204,  0.03798797, ..., -0.080321  ,
        -0.1193777 ,  0.00596426],
       [ 0.01246224,  0.01364668,  0.04105236, ..., -0.07725951,
        -0.13012475,  0.01362491],
       [ 0.01581116,  0.0131523 ,  0.04183232, ..., -0.07409089,
        -0.12856905,  0.01441113]], dtype=float32)

In [8]:
import faiss, numpy as np

X = np.asarray(embeddings, dtype="float32")
faiss.normalize_L2(X)

index = faiss.IndexFlatIP(X.shape[1])
index.add(X)                      

In [9]:
index

<faiss.swigfaiss_avx2.IndexFlatIP; proxy of <Swig Object of type 'faiss::IndexFlatIP *' at 0x0000011B20686B20> >

In [10]:
def retrieve(query, k=5):
    q = embedder.encode([query]).astype("float32")
    faiss.normalize_L2(q)
    scores, idx = index.search(q, k)      # scores in [0,1] ~ cosine
    return [(int(i), float(s)) for i, s in zip(idx[0], scores[0])]


In [11]:
ex_1 = "what are the best BYOD plans in Virgin plus below 60$"

pair_1 = retrieve(ex_1)
print(pair_1)

[(65, 0.7283002138137817), (59, 0.7259033918380737), (67, 0.7257879376411438), (9, 0.725434422492981), (68, 0.725420355796814)]


In [12]:
#from huggingface_hub import notebook_login

#notebook_login()

In [13]:
#pip install hf_xet

In [14]:
from transformers import pipeline, AutoTokenizer, AutoModelForSeq2SeqLM

tokenizer = AutoTokenizer.from_pretrained("MBZUAI/LaMini-Flan-T5-783M")
model = AutoModelForSeq2SeqLM.from_pretrained("MBZUAI/LaMini-Flan-T5-783M")
qa_pipeline = pipeline("text2text-generation",model = model, tokenizer = tokenizer)
pipeline

tokenizer_config.json: 0.00B [00:00, ?B/s]

E:\Anaconda\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\kompe\.cache\huggingface\hub\models--MBZUAI--LaMini-Flan-T5-783M. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


spiece.model:   0%|          | 0.00/792k [00:00<?, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

special_tokens_map.json: 0.00B [00:00, ?B/s]

...

pytorch_model.bin:   0%|          | 0.00/3.13G [00:00<?, ?B/s]

generation_config.json:   0%|          | 0.00/147 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/3.13G [00:00<?, ?B/s]

Device set to use cuda:0


<function transformers.pipelines.pipeline(task: Optional[str] = None, model: Union[str, ForwardRef('PreTrainedModel'), ForwardRef('TFPreTrainedModel'), NoneType] = None, config: Union[str, transformers.configuration_utils.PretrainedConfig, NoneType] = None, tokenizer: Union[str, transformers.tokenization_utils.PreTrainedTokenizer, ForwardRef('PreTrainedTokenizerFast'), NoneType] = None, feature_extractor: Union[str, ForwardRef('SequenceFeatureExtractor'), NoneType] = None, image_processor: Union[str, transformers.image_processing_utils.BaseImageProcessor, NoneType] = None, processor: Union[str, transformers.processing_utils.ProcessorMixin, NoneType] = None, framework: Optional[str] = None, revision: Optional[str] = None, use_fast: bool = True, token: Union[str, bool, NoneType] = None, device: Union[int, str, ForwardRef('torch.device'), NoneType] = None, device_map: Union[str, dict[str, Union[int, str]], NoneType] = None, torch_dtype: Union[str, ForwardRef('torch.dtype'), NoneType] = 'a

In [15]:
def answer_question(query):
    top_k = retrieve(query, k=5)
    context = "\n".join([plan_data_mod[i]["Description"] for i, _ in top_k])
    prompt = (
    f"You are a telecom assistant helping a user choose the best phone plan. "
    f"Only include plans that match the question clearly. Be concise and friendly.\n\n"
    f"Plans:\n{context}\n\n"
    f"Question: {query}\n"
    f"Answer in full sentences:"
)

    response = qa_pipeline(prompt, max_new_tokens=100, do_sample=False)
    raw_answer = response[0]['generated_text']

    lines = raw_answer.strip().split('\n')
    unique_lines = list(dict.fromkeys(lines))
    cleaned_answer = "\n".join(unique_lines)

    return cleaned_answer


In [19]:
import evaluate
rouge = evaluate.load("rouge")
bleu = evaluate.load("bleu")
bertscore = evaluate.load("bertscore")

def eval_metrics(prediction: str, reference: str):
    bleu_res  = bleu.compute(predictions=[prediction], references=[reference])
    rouge_res = rouge.compute(predictions=[prediction], references=[reference])
    bert_res  = bertscore.compute(predictions=[prediction], references=[reference], lang="en")
    return {
        "BLEU": bleu_res["bleu"],
        "ROUGE-1": rouge_res["rouge1"],
        "ROUGE-2": rouge_res["rouge2"],
        "ROUGE-L": rouge_res["rougeL"],
        "BERTScore-F1": float(sum(bert_res["f1"]) / len(bert_res["f1"]))
    }

In [20]:
while True:
    user_query = input("Ask your plan-related question: ")
    if user_query.strip().lower() in ["exit", "quit"]:
        print("\n\nGoodbye!")
        break

    answer = answer_question(user_query)
    print("\nAnswer:\n", answer)
    
    prediction = answer
    top1 = retrieve(user_query, k=1)
    reference = plan_data_mod[top1[0][0]]["Description"] if top1 else ""

    scores = eval_metrics(prediction, reference)
    print("Evaluation:")
    print(f"BLEU: {scores['BLEU']:.4f} | ROUGE-1: {scores['ROUGE-1']:.4f} | "
          f"ROUGE-2: {scores['ROUGE-2']:.4f} | ROUGE-L: {scores['ROUGE-L']:.4f} | "
          f"BERTScore-F1: {scores['BERTScore-F1']:.4f}")
    print("\n" + "-"*50 + "\n")


Ask your plan-related question: bell student plan in alberta?

Answer:
 Bell offers three student plans in Alberta: Elite Lite for $52 a month, Elite Lite for $35 a month, ExtraElite+ for $55 a month, and ExtraElite for $45 a month. These plans are for hardware upgrade customers only and include unlimited data with device financing over 24 months and data-sharing with Hotspot.


tokenizer_config.json:   0%|          | 0.00/25.0 [00:00<?, ?B/s]

E:\Anaconda\Lib\site-packages\huggingface_hub\file_download.py:143: UserWarning: `huggingface_hub` cache-system uses symlinks by default to efficiently store duplicated files but your machine does not support them in C:\Users\kompe\.cache\huggingface\hub\models--roberta-large. Caching files will still work but in a degraded version that might require more space on your disk. This warning can be disabled by setting the `HF_HUB_DISABLE_SYMLINKS_WARNING` environment variable. For more details, see https://huggingface.co/docs/huggingface_hub/how-to-cache#limitations.
To support symlinks on Windows, you either need to activate Developer Mode or to run Python as an administrator. In order to activate developer mode, see this article: https://docs.microsoft.com/en-us/windows/apps/get-started/enable-your-device-for-development
  warnings.warn(message)


config.json:   0%|          | 0.00/482 [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.36M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/1.42G [00:00<?, ?B/s]

Some weights of RobertaModel were not initialized from the model checkpoint at roberta-large and are newly initialized: ['pooler.dense.bias', 'pooler.dense.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


Evaluation:
BLEU: 0.2613 | ROUGE-1: 0.5745 | ROUGE-2: 0.3478 | ROUGE-L: 0.4043 | BERTScore-F1: 0.9322

--------------------------------------------------

Ask your plan-related question: cheapest plan in virgin plus byod?

Answer:
 The cheapest plan in Virgin Plus byod is BYOP 40GB (Student, Alberta) for the price of $39 a month, which includes Unlimited data with BYOD and allows you to data-share with Hotspot. This plan is for hardware upgrade customers only.
Evaluation:
BLEU: 0.8449 | ROUGE-1: 0.9114 | ROUGE-2: 0.8571 | ROUGE-L: 0.8861 | BERTScore-F1: 0.9670

--------------------------------------------------

Ask your plan-related question: lucky plan under 30$?

Answer:
 Yes, Lucky offers a plan under $30 for the Student, Alberta plan which includes Unlimited data with BYOD and does not include data-share with Hotspot.
Evaluation:
BLEU: 0.3511 | ROUGE-1: 0.6667 | ROUGE-2: 0.5574 | ROUGE-L: 0.6349 | BERTScore-F1: 0.9292

--------------------------------------------------

Ask your p

In [21]:
tokenizer.save_pretrained("Plan_Retrieval_RAG")
model.save_pretrained("RAG_based_Model")

In [22]:
faiss.write_index(index, "RAG_model.index")
np.save("plan_embeddings.npy", embeddings)